<a href="https://colab.research.google.com/github/SinSham/Medlr-assignment/blob/main/Medlr_Assignment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd
import re
from sklearn.impute import KNNImputer
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

In [2]:
df = pd.read_csv('/content/medlr_assignment_dataset.csv')

In [3]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

In [4]:
df.head()

id                          name    source  \
0  source_6-75716               Dolo 1gm Tablet  source_6   
1  source_2-39579          Dolo 1000mg Infusion  source_2   
2  source_7-90343            Dolo 1000mg Tablet  source_7   
3  source_1-65076      Dolo 1000 mg Tablet 10's  source_1   
4  source_1-65077  Dolo 120 mg Suspension 60 ml  source_1   

   prescription_required  retail_price  discounted_price    manufacturer  \
0                  False         45.58             40.11      micro labs   
1                   True        268.00            219.76  micro labs ltd   
2                  False         45.58             35.10  micro labs ltd   
3                   True         45.50             40.00  micro labs ltd   
4                  False         40.00             35.20  micro labs ltd   

                  quantity       packaging_form  \
0    10 Tablet(s) in Strip                STRIP   
1                      NaN                  NaN   
2  10.0 tablets in 1 strip                  NaN   
3                       10       Strip | Tablet   
4                       60  Bottle | Suspension   

                                salts  
0  Paracetamol / Acetaminophen(1.0 G)  
1    Paracetamol/Acetaminophen 1000mg  
2                Paracetamol (1000mg)  
3                  PARACETAMOL-1000MG  
4                   PARACETAMOL-120MG

In [5]:
df.shape

(1448, 10)

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1448 entries, 0 to 1447
Data columns (total 10 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   id                     1448 non-null   object 
 1   name                   1448 non-null   object 
 2   source                 1448 non-null   object 
 3   prescription_required  1448 non-null   bool   
 4   retail_price           1367 non-null   float64
 5   discounted_price       1384 non-null   float64
 6   manufacturer           1446 non-null   object 
 7   quantity               1184 non-null   object 
 8   packaging_form         931 non-null    object 
 9   salts                  1389 non-null   object 
dtypes: bool(1), float64(2), object(7)
memory usage: 103.4+ KB


## Creating two new columns called "dosage form" to store the medicine type and "base name" for medicine's base name

In [7]:
dosage_forms = [
    "tablet", "capsule", "powder", "solution", "emulsion", "suspension", "syrup", "infusion", "ointment", "cream", "gel", "lotion", "spray", "injection",
    "eye drop", "ear drop", "nasal drop", "paint", "liquid", "soap", "shampoo", "sachet"]

In [8]:
def clean_and_extract(row):
    text = row.lower()
    text = ' '.join(text.split())
    text = text.replace('-', ' ')
    text = re.sub(r"s\b", '', text)

    # Extract Base Name
    base_name = text.split()[0]

    # Extract Dosage Form
    dosage_form = ''
    for form in dosage_forms:
        if form in text:
            dosage_form = form
            break

    return pd.Series([base_name, dosage_form])


df[['base name', 'dosage form']] = df['name'].apply(clean_and_extract)

In [9]:
df['base name'].unique()

array(['dolo', 'doloact', 'doloage', 'doloar', 'dolobak', 'doloban',
       'dolobest', 'dolobid', 'dolobrake', 'doloby', 'dolocaf',
       'dolocaine', 'dolocalm', 'dolocam', 'dolocare', 'dolocef',
       'dolocel', 'dolocem', 'dolocerin', 'dolocet', 'dolochek',
       'dolocide', 'dolocip', 'doloco', 'dolocold', 'dolocrat',
       'dolocure', 'dolocute', 'dolodart', 'dolodase', 'dolodik',
       'dolodil', 'dolodol', 'dolodor', 'doloend', 'dolofab', 'dolofan',
       'dolofen', 'dolofenac', 'dolofin', 'dolofirst', 'doloflam',
       'doloflex', 'doloforce', 'dolofort', 'doloforte', 'dolofresh',
       'dologaba', 'dologel', 'dologen', 'dologesic', 'dologin',
       'dologlan', 'dolohit', 'doloid', 'doloja', 'dolojoy', 'dolojust',
       'dolokam', 'doloket', 'dolokim', 'dolokind', 'dolokoff', 'dololax',
       'dololsac', 'dololup', 'dolomade', 'dolomark', 'doloma', 'dolomax',
       'dolomec', 'dolomed', 'dolomeg', 'dolomet', 'dolomide', 'dolomine',
       'dolomol', 'dolomon', 'dol

In [10]:
df['base name'].nunique()

243

In [11]:
df.loc[df['base name'].isin(['ibuprofen(alk)', 'ibuprofen(cip)']), 'base name'] = 'ibuprofen'

In [12]:
df['base name'].nunique()

242

In [13]:
df.head()

id                          name    source  \
0  source_6-75716               Dolo 1gm Tablet  source_6   
1  source_2-39579          Dolo 1000mg Infusion  source_2   
2  source_7-90343            Dolo 1000mg Tablet  source_7   
3  source_1-65076      Dolo 1000 mg Tablet 10's  source_1   
4  source_1-65077  Dolo 120 mg Suspension 60 ml  source_1   

   prescription_required  retail_price  discounted_price    manufacturer  \
0                  False         45.58             40.11      micro labs   
1                   True        268.00            219.76  micro labs ltd   
2                  False         45.58             35.10  micro labs ltd   
3                   True         45.50             40.00  micro labs ltd   
4                  False         40.00             35.20  micro labs ltd   

                  quantity       packaging_form  \
0    10 Tablet(s) in Strip                STRIP   
1                      NaN                  NaN   
2  10.0 tablets in 1 strip                  NaN   
3                       10       Strip | Tablet   
4                       60  Bottle | Suspension   

                                salts base name dosage form  
0  Paracetamol / Acetaminophen(1.0 G)      dolo      tablet  
1    Paracetamol/Acetaminophen 1000mg      dolo    infusion  
2                Paracetamol (1000mg)      dolo      tablet  
3                  PARACETAMOL-1000MG      dolo      tablet  
4                   PARACETAMOL-120MG      dolo  suspension

## Cleaning column "name"

In [14]:
df['name'] = df['name'].str.lower()
df['name'] = df['name'].apply(lambda x: re.sub(r'[^a-z0-9\'/\s]', '', x))  # Remove special characters except apostrophe and '/'
df['name'] = df['name'].str.replace(r'\s+', ' ', regex=True).str.strip()

In [15]:
def add_space_number_unit(text):
    return re.sub(r'(\d+)([a-zA-Z]+)', r'\1 \2', text)

df['name'] = df['name'].apply(lambda x: add_space_number_unit(x))

In [16]:
df["name"]

0                                                                                                                                dolo 1 gm tablet
1                                                                                                                           dolo 1000 mg infusion
2                                                                                                                             dolo 1000 mg tablet
3                                                                                                                        dolo 1000 mg tablet 10's
4                                                                                                                    dolo 120 mg suspension 60 ml
5                                                                                                                    dolo 120 mg suspension 60 ml
6                                                                                                                             dolo 120 suspension
7                                                                                                                           dolo 156 mg syp 60 ml
8                                                                                                                        dolo 15625 mg suspension
9                                                                                                                       dolo 15625 mg syrup 60 ml
10                                                                                                                   dolo 250 mg suspension 60 ml
11                                                                                                                          dolo 250 mg syp 60 ml
12                                                                                                                       dolo 250 oral suspension
13                                                                                                                     dolo 250 suspension 100 ml
14                                                                                                                      dolo 250 suspension 60 ml
15                                                                                                                dolo 500 mg strip of 10 tablets
16                                                                                                                dolo 500 mg strip of 15 tablets
17                                                                                                                          dolo 500 mg tab 1 x15
18                                                                                                                                dolo 500 tablet
19                                                                                                                           dolo 500 tablet 10's
20                                                                                                                            dolo500 tablet 15's
21                                                                                                                dolo 650 mg strip of 10 tablets
22                                                                                                                dolo 650 mg strip of 15 tablets
23                                                                                                                                dolo 650 tablet
24                                                                                                                            dolo650 tablet 15's
25                                                                                                                 dolo ampoule of 2 ml injection
26                                                                                                                      dolo bottle of 5 ml drops
27                                                        

## Filling dosage form column using information from name column

In [17]:
df[df['dosage form'] == ""]

id  \
7       source_3-2151   
11      source_3-2152   
17      source_3-2153   
26     source_6-75724   
35     source_7-90348   
47     source_1-65088   
49     source_1-65089   
83     source_1-65097   
97     source_6-75758   
118    source_6-75769   
255     source_3-2154   
344     source_3-2156   
350     source_3-2157   
353     source_3-2158   
436    source_2-39684   
440    source_1-65191   
489     source_3-2159   
566    source_2-39716   
567    source_1-65232   
626    source_1-65249   
760    source_2-39773   
762    source_6-76010   
763    source_7-90627   
841    source_6-76040   
846    source_6-76043   
873     source_3-2161   
877     source_3-2162   
897    source_1-65316   
900     source_3-2163   
913    source_7-90687   
946     source_3-6189   
951     source_3-6190   
957     source_3-6191   
963    source_2-96312   
964   source_1-158206   
984     source_3-9076   
991     source_3-9077   
997     source_3-9078   
1013    source_3-9079   
1018    source_3-9080   
1022  source_2-136315   
1024    source_3-9081   
1028    source_3-9082   
1033    source_3-9083   
1038    source_3-9084   
1082  source_1-144845   
1124    source_3-6901   
1129    source_3-6902   
1156    source_3-6903   
1166    source_3-6904   
1170  source_1-142250   
1171   source_2-82905   
1174  source_6-184554   
1176    source_3-5750   
1187    source_3-5751   
1206  source_1-149278   
1251  source_1-103909   
1252  source_6-125694   
1253  source_1-103910   
1254  source_1-103911   
1255  source_6-125695   
1256  source_1-103912   
1257  source_7-147465   
1258  source_6-125696   
1259  source_1-103913   
1260   source_2-62055   
1262  source_1-103914   
1263  source_1-103915   
1273    source_3-9198   
1288    source_3-9199   
1294    source_3-9200   
1298    source_3-9201   
1301    source_3-9202   
1308  source_1-226969   
1352  source_2-137407   
1353   source_5-47740   
1354    source_3-9204   
1371  source_7-238064   
1402   source_2-96301   
1410   source_2-28249   
1411   source_1-45425   
1432    source_3-6692   

                                                              name    source  \
7                                            dolo 156 mg syp 60 ml  source_3   
11                                           dolo 250 mg syp 60 ml  source_3   
17                                           dolo 500 mg tab 1 x15  source_3   
26                                       dolo bottle of 5 ml drops  source_6   
35                                                      dolo drops  source_7   
47                                               dolomf susp 60 ml  source_1   
49                                           dolo oral drops 15 ml  source_1   
83                                              doloar sp tab 10's  source_1   
97                                          doloban plus vet bolus  source_6   
118                                           dolobid m oint 30 gm  source_6   
255                                   doloforce dt 10 mg tab 1 x10  source_3   
344                                         dolokind spas inj 1 ml  source_3   
350                                        dolokind spas tab 1 x10  source_3   
353                                          dolokind sr tab 1 x10  source_3   
436                                              dolomol iv 100 ml  source_2   
440                                   dolomor cold susension 60 ml  source_1   
489                                     dolonex dt 20 mg tab 1 x15  source_3   
566                                                  dolopar drops  source_2   
567                                            dolopar drops 15 ml  source_1   
626                                               doloral tab 10's  source_1   
760                                     dolospas 20 mg/500 mg drop  source_2   
762                                                 dolospas drops  source_6   
763                                       dolospas spas oral drops  source_7   
841                    

In [18]:
# Update dosage form based on 'tab' or 'syp' in the 'name' column
def fill_dosage_form_simple(row):
    if 'syp' in row['name'].lower():
        return 'syrup'
    elif 'tab' in row['name'].lower():
        return 'tablet'
    elif 'susp' in row['name'].lower():
        return 'suspension'
    elif 'oint' in row['name'].lower():
        return 'ointment'
    elif 'inj' in row['name'].lower():
        return 'injection'
    # If no match, keep the existing value (or return NaN if preferred)
    return row['dosage form']

# Apply the function to the DataFrame
df['dosage form'] = df.apply(fill_dosage_form_simple, axis=1)

In [19]:
df[df['dosage form'] == ""]

id  \
26     source_6-75724   
35     source_7-90348   
49     source_1-65089   
97     source_6-75758   
436    source_2-39684   
440    source_1-65191   
566    source_2-39716   
567    source_1-65232   
760    source_2-39773   
762    source_6-76010   
763    source_7-90627   
846    source_6-76043   
913    source_7-90687   
963    source_2-96312   
964   source_1-158206   
1174  source_6-184554   
1206  source_1-149278   
1251  source_1-103909   
1252  source_6-125694   
1253  source_1-103910   
1254  source_1-103911   
1255  source_6-125695   
1256  source_1-103912   
1257  source_7-147465   
1258  source_6-125696   
1259  source_1-103913   
1260   source_2-62055   
1262  source_1-103914   
1263  source_1-103915   
1308  source_1-226969   
1352  source_2-137407   
1353   source_5-47740   
1371  source_7-238064   
1411   source_1-45425   

                                                              name    source  \
26                                       dolo bottle of 5 ml drops  source_6   
35                                                      dolo drops  source_7   
49                                           dolo oral drops 15 ml  source_1   
97                                          doloban plus vet bolus  source_6   
436                                              dolomol iv 100 ml  source_2   
440                                   dolomor cold susension 60 ml  source_1   
566                                                  dolopar drops  source_2   
567                                            dolopar drops 15 ml  source_1   
760                                     dolospas 20 mg/500 mg drop  source_2   
762                                                 dolospas drops  source_6   
763                                       dolospas spas oral drops  source_7   
846                                             doloviz drops 5 ml  source_6   
913                                           doloxy cv oral drops  source_7   
963                                                  paracip drops  source_2   
964                                            paracip drops 15 ml  source_1   
1174                                     oflomac 03 e/e drops 5 ml  source_6   
1206                                             oflomac iv 100 ml  source_1   
1251                                                  insupen blue  source_1   
1252                                             insupen ez device  source_6   
1253                                            insupen ez pen 1's  source_1   
1254                                                  insupen gold  source_1   
1255                                         insupen gold ease pen  source_6   
1256        insupen probasalog refil 100 iu 5 x3 ml initiation kit  source_1   
1257               insupen pro insugen 30/70 refill initiation kit  source_7   
1258                                  insupen pro device 1 numbers  source_6   
1259                                             insupen pro green  source_1   
1260                                               insupen pro pen  source_2   
1262  insupen pro plus insugen 30/70 refil initiation kit 5 x 3 ml  source_1   
1263                                               insupen red 1's  source_1   
1308                                              zocon drops 5 ml  source_1   
1352                                                    zocont kit  source_2   
1353                                               zocon t kit 1's  source_5   
1371                             piconext plus laxative sugar free  source_7   
1411                                  ciprofloxacin iv core 100 ml  source_1   

      prescription_required  retail_price  discounted_price  \
26                    False         27.00            27.000   
35                    False         30.07            22.500   
49                    False         30.00            26.400   
97                     True         28.00            24.640   
436                    True

In [20]:
df.iloc[[26, 35, 49, 440, 566, 567], df.columns.get_loc('dosage form')] = 'suspension'
df.iloc[97, df.columns.get_loc('dosage form')] = 'bolus'
df.iloc[1174, df.columns.get_loc('dosage form')] = 'eye and ear drop'
df.iloc[[846, 1308], df.columns.get_loc('dosage form')] = 'eye drop'
df.iloc[[760, 762, 763, 913], df.columns.get_loc('dosage form')] = 'oral drop'
df.iloc[[963, 964], df.columns.get_loc('dosage form')] = 'solution'
df.iloc[[436, 1206, 1411], df.columns.get_loc('dosage form')] = 'infusion'
df.iloc[[1251, 1252, 1253, 1254, 1255, 1256, 1257, 1258, 1259, 1260, 1262, 1263], df.columns.get_loc('dosage form')] = 'device'
df.iloc[[1352, 1353], df.columns.get_loc('dosage form')] = 'tablet'
df.iloc[1371, df.columns.get_loc('dosage form')] = 'emulsion'

In [21]:
df[df['dosage form'] == ""] #checking if still empty rows in dosage form

Empty DataFrame
Columns: [id, name, source, prescription_required, retail_price, discounted_price, manufacturer, quantity, packaging_form, salts, base name, dosage form]
Index: []

In [22]:
df['dosage form'].nunique()

26

## Cleaning "manufacturer" column

In [23]:
print(df['manufacturer'].unique())

['micro labs' 'micro labs ltd' 'integra life sciences pvt ltd'
 'bosch pharmaceuticals pvt ltd' 'mankind pharmaceuticals ltd'
 'medico health care' 'gujarat liqui pharmacaps pvt ltd'
 'bioguard organics ltd' 'ochoa laboratories ltd'
 'ochoa laboratiories ltd' 'bmw pharmaco india pvt ltd' 'allenge india'
 'allenge india pharmaceuticals pvt ltd' 'unibiotech health care pvt ltd'
 'mankind pharma ltd' 'mankind pharma pvt ltd' 'ttk healthcare ltd'
 'ttk healthcare' 'apotex life sciences' 'apotex pharmachem india pvt ltd'
 'boyeger biotech pvt ltd' 'hnf care pvt ltd' 'cadila pharmaceuticals ltd'
 'zydus healthcare ltd' 'zydus cadila healthcare ltd'
 'cadila healthcare ltd' 'sanes pharmaceuticals' 'sresan pharmaceuticals'
 'cipla ltd' 'bhavishya pharmaceuticals pvt ltd' 'alkem laboratories ltd'
 'eurocare' 'vensat bio' 'dolphin laboratories'
 'dolphin healthcare pvt ltd' 'cian health care pvt ltd'
 'netprime pharma pvt ltd' 'zydus cadila' 'caplet india pvt ltd'
 'indoco remedies ltd' 'kee pha

In [24]:
# Check for missing or empty values in the 'manufacturer' column
missing_values = df[df['manufacturer'].isna() | (df['manufacturer'].str.strip() == '')]
missing_values

id                 name    source  prescription_required  \
206  source_6-75804  dolodol p tablet 10  source_6                   True   
831  source_6-76036     dolour x tablets  source_6                   True   

     retail_price  discounted_price manufacturer               quantity  \
206        313.47            275.85          NaN  15 Tablet(s) in Strip   
831         53.00             46.64          NaN  10 Tablet(s) in Strip   

    packaging_form                      salts base name dosage form  
206          STRIP     Paracetamol + Tramadol   dolodol      tablet  
831          STRIP  Aceclofenac + Paracetamol    dolour      tablet

In [25]:
df['manufacturer'].fillna("unknown", inplace=True)

In [26]:
def clean_manufacturer(name):
    name = name.lower()
    name = re.sub(r'\b(pvt|ltd|gx|llp)\b', '', name) #removing suffixes like "ltd", "pvt", "gx", "llp"
    name = re.sub(r'[^a-z0-9\s]', '', name)
    name = ' '.join(name.split())

    return name.strip()


df['manufacturer'] = df['manufacturer'].apply(clean_manufacturer)

In [27]:
df['manufacturer'] = df['manufacturer'].replace({
    r'\b(company|pharma|labs|laboratories|pharmaceuticals|industries|drugs|drug|pharmaceutical|pharmacy|laboratorie|pharma|life science|lifescience|lifesciences|life sciences|health care|healthcare|health product|health products|india|life care|therapeutics|therapeutic|pharmachem|pharmaco|pharmacaps|biotech|innovations|innovation)\b': ''
}, regex=True)

df['manufacturer'] = df['manufacturer'].apply(lambda x: ' '.join(x.split()).strip())

## Fixing spelling errors in names of manufacturer

In [28]:
df['manufacturer'] = df['manufacturer'].replace({"v m s": "vms"}, regex=True)
df['manufacturer'] = df['manufacturer'].replace({"f d c": "fdc"}, regex=True)
df['manufacturer'] = df['manufacturer'].replace({"m d": "md"}, regex=True)
df['manufacturer'] = df['manufacturer'].replace({"made inn": "madeinn"}, regex=True)
df['manufacturer'] = df['manufacturer'].replace({"galenis": "galenus"}, regex=True)
df['manufacturer'] = df['manufacturer'].replace({"mundi pharma": "mundipharma"}, regex=True)
df['manufacturer'] = df['manufacturer'].replace({"saviour": "savior"}, regex=True)

## Fixing inconsistent names

In [29]:
df["manufacturer"] = df["manufacturer"].astype(str).apply(lambda x: "zydus" if "zydus" in x else x)

In [30]:
df["manufacturer"] = df["manufacturer"].astype(str).apply(lambda x: "cadila" if "cadila" in x else x)

In [31]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'cipla' if 'cipla' in x else x)

In [32]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'ochoa' if 'ochoa' in x else x)

In [33]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'aerochem neutron' if 'aero chem neutron' in x else x)

In [34]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'tulip' if 'tulip' in x else x)

In [35]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'dolvis' if 'dolvis' in x else x)

In [36]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'dr reddy' if 'dr reddy' in x else x)

In [37]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'dr jrk' if 'dr jrk' in x else x)

In [38]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'winmark' if 'winmark' in x else x)

In [39]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'pfizer' if ('pfizer' in x or 'phizer' in x) else x)

In [40]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'mars chemicals' if 'mars' in x else x)

In [41]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'troikaa' if 'triokaa' in x else x)

In [42]:
df['manufacturer'] = df['manufacturer'].astype(str).apply(lambda x: 'hegde and hegde' if 'hegde' in x else x)

In [43]:
sorted_manufacturers = pd.DataFrame(sorted(df['manufacturer'].unique()), columns=['Manufacturer'])

print(sorted_manufacturers)

                          Manufacturer
0                                   3m
1                              aarotax
2                               abbott
3                                acron
4                                 acto
5                        adcock ingram
6                               adinos
7                     aerochem neutron
8                             aerozest
9                       agron remedies
10                               ajapa
11                        albert david
12                            alienist
13                             alisier
14                               alkem
15                             allenge
16                                alpa
17                      alpic remedies
18                               amwin
19                              anevay
20                                anvi
21                              apotex
22                               aptus
23                               ardor
24                       

## Removing inconsistencies from "Quantity" column

In [44]:
df.loc[df['dosage form'] == 'tablet', 'quantity'] = df.loc[df['dosage form'] == 'tablet', 'quantity'] \
    .str.extract(r'(\d+)', expand=False).astype(float)

# For rows where quantity is NaN, leave them as NaN, otherwise apply transformation
df.loc[df['dosage form'] == 'tablet', 'quantity'] = df.loc[df['dosage form'] == 'tablet', 'quantity'] \
    .apply(lambda x: f"{int(x)} tablets" if pd.notna(x) else None)

In [45]:
df.loc[df['dosage form'] == 'capsule', 'quantity'] = df.loc[df['dosage form'] == 'capsule', 'quantity'] \
    .str.extract(r'(\d+)', expand=False).astype(float)

# For rows where quantity is NaN, leave them as NaN, otherwise apply transformation
df.loc[df['dosage form'] == 'capsule', 'quantity'] = df.loc[df['dosage form'] == 'capsule', 'quantity'] \
    .apply(lambda x: f"{int(x)} capsules" if pd.notna(x) else None)  # Keep NaN as NaN, otherwise append 'tablets'

In [46]:
ml_dosage_forms = ["solution", "emulsion", "suspension", "syrup", "infusion",
                "lotion", "eye drop", "ear drop", "nasal drop", "paint",
                "liquid", "shampoo", "oral drop", "eye and ear drop"]

df.loc[df['dosage form'].isin(ml_dosage_forms), 'quantity'] = df.loc[df['dosage form'].isin(ml_dosage_forms), 'quantity'] \
    .str.extract(r'(\d+(\.\d+)?)', expand=False)[0]

df.loc[df['dosage form'].isin(ml_dosage_forms), 'quantity'] = df.loc[df['dosage form'].isin(ml_dosage_forms), 'quantity'] \
    .apply(lambda x: f"{float(x):.1f} ml" if pd.notna(x) else None)

In [47]:
g_dosage_forms = ["powder", "ointment", "cream", "gel", "spray", "soap", "sachet"]

df.loc[df['dosage form'].isin(g_dosage_forms), 'quantity'] = df.loc[df['dosage form'].isin(g_dosage_forms), 'quantity'] \
    .str.extract(r'(\d+(\.\d+)?)', expand=False)[0]

df.loc[df['dosage form'].isin(g_dosage_forms), 'quantity'] = df.loc[df['dosage form'].isin(g_dosage_forms), 'quantity'] \
    .apply(lambda x: f"{float(x):.1f} g" if pd.notna(x) else None)

In [48]:
exclude_rows = [485, 904, 1067, 1167, 1168, 1261] # these are exceptions so handling them separately

# Apply transformation to all rows with 'injection' except for the ones in exclude_rows
df.loc[~df.index.isin(exclude_rows) & (df['dosage form'] == 'injection'), 'quantity'] = \
    df.loc[~df.index.isin(exclude_rows) & (df['dosage form'] == 'injection'), 'quantity'] \
    .str.extract(r'(\d+)', expand=False).astype(float)

# For rows where quantity is NaN, leave them as NaN, otherwise apply transformation
df.loc[~df.index.isin(exclude_rows) & (df['dosage form'] == 'injection'), 'quantity'] = \
    df.loc[~df.index.isin(exclude_rows) & (df['dosage form'] == 'injection'), 'quantity'] \
    .apply(lambda x: f"{int(x)} ml" if pd.notna(x) else None)

In [49]:
df.loc[[485, 904], 'quantity'] = '10 ml'
df.loc[[1261], 'quantity'] = '15 ml'
df.loc[[1067], 'quantity'] = '2 ml'
df.loc[[1167, 1168], 'quantity'] = '10 mg'

In [50]:
df.loc[[485, 904, 1067, 1167, 1168, 1261]]

id  \
485    source_1-65210   
904    source_1-65318   
1067    source_4-1166   
1167  source_6-172175   
1168    source_4-4074   
1261  source_6-125697   

                                                         name    source  \
485                       dolonex 40 mg im injection 5 x 2 ml  source_1   
904                              doloxicam injection 5 x 2 ml  source_1   
1067                                  celtere 80 mg injection  source_4   
1167          neovec 10 mg dry vial of 1 powder for injection  source_6   
1168                                   neovec 10 mg injection  source_4   
1261  insupen pro plus insugen 30/70 refil box of 1 injection  source_6   

      prescription_required  retail_price  discounted_price      manufacturer  \
485                    True        320.00            281.60            pfizer   
904                    True        265.00            233.20           troikaa   
1067                   True      15070.00           1919.00             celon   
1167                   True        109.50             96.36              neon   
1168                   True        122.75            104.00              neon   
1261                   True       1450.00           1290.50  biocon biologics   

     quantity      packaging_form  \
485     10 ml     Box | Injection   
904     10 ml  Packet | Injection   
1067     2 ml                VIAL   
1167    10 mg            DRY VIAL   
1168    10 mg                VIAL   
1261    15 ml                 BOX   

                                             salts  base name dosage form  
485                                 PIROXICAM-40MG    dolonex   injection  
904                                 PIROXICAM-20MG  doloxicam   injection  
1067                                     DOCETAXEL    celtere   injection  
1167                           Vecuronium(10.0 Mg)     neovec   injection  
1168                            VECURONIUM BROMIDE     neovec   injection  
1261  Human Insulin / Soluble Insulin(100.0 Iu/Ml)    insupen   injection

## Standardizing "salts" column

In [51]:
df['salts']

0                                                                                                                     Paracetamol / Acetaminophen(1.0 G)
1                                                                                                                       Paracetamol/Acetaminophen 1000mg
2                                                                                                                                   Paracetamol (1000mg)
3                                                                                                                                     PARACETAMOL-1000MG
4                                                                                                                                      PARACETAMOL-120MG
5                                                                                                              Paracetamol / Acetaminophen(120.0 Mg/5ml)
6                                                                                                                    Paracetamol/Acetaminophen 120mg/5ml
7                                                                                                               PARACETAMOL/ACETAMINOPHEN 156.25 MG /5ML
8                                                                                                                             Paracetamol (156.25mg/5ml)
9                                                                                                                                   PARACETAMOL-156.25MG
10                                                                                                                 Paracetamol / Acetaminophen(250.0 Mg)
11                                                                                                                 PARACETAMOL/ACETAMINOPHEN 250 MG /5ML
12                                                                                                                               Paracetamol (250mg/5ml)
13                                                                                                                                     PARACETAMOL-250MG
14                                                                                                                                     PARACETAMOL-250MG
15                                                                                                                 Paracetamol / Acetaminophen(500.0 Mg)
16                                                                                                                 Paracetamol / Acetaminophen(500.0 Mg)
17                                                                                                                      PARACETAMOL/ACETAMINOPHEN 500 MG
18                                                                                                                                     Paracetamol 500mg
19                                                                                                                                     PARACETAMOL-500MG
20                                                                                                                                     PARACETAMOL-500MG
21                                                                                                                 Paracetamol / Acetaminophen(650.0 Mg)
22                                                                                                                 Paracetamol / Acetaminophen(650.0 Mg)
23                                                                                                                                     Paracetamol 650mg
24                                                                                                                                     PARACETAMOL-650MG
25                                                                                                                 Paracetamol / Acetaminophen(150.0 Mg)
26                    

In [52]:
df['salts'] = df['salts'].astype(str).str.lower()  # Convert to string and lowercase
df['salts'] = df['salts'].replace(r'(\d+(\.\d+)?)', r' \1 ', regex=True)  # Add space around numbers
df['salts'] = df['salts'].replace('\+', '/', regex=True)  # Replace '+' with '/'
df['salts'] = df['salts'].replace(',', '/', regex=True) # Replace ',' with '/'
df['salts'] = df['salts'].str.replace(r'[()-]', '', regex=True)  # Remove parentheses and hyphens
df['salts'] = df['salts'].replace(r'\s*/\s*', '/', regex=True)  # Remove whitespace around '/'

df['salts'] = df['salts'].apply(lambda x: ' '.join([f"{float(i):.1f}" if i.replace('.', '', 1).isdigit() else i for i in x.split()]))

In [53]:
df['salts']

0                                                                                                                                                      paracetamol/acetaminophen 1.0 g
1                                                                                                                                                  paracetamol/acetaminophen 1000.0 mg
2                                                                                                                                                                paracetamol 1000.0 mg
3                                                                                                                                                                paracetamol 1000.0 mg
4                                                                                                                                                                 paracetamol 120.0 mg
5                                                                                                                                              paracetamol/acetaminophen 120.0 mg/5 ml
6                                                                                                                                              paracetamol/acetaminophen 120.0 mg/5 ml
7                                                                                                                                              paracetamol/acetaminophen 156.2 mg/5 ml
8                                                                                                                                                            paracetamol 156.2 mg/5 ml
9                                                                                                                                                                 paracetamol 156.2 mg
10                                                                                                                                                  paracetamol/acetaminophen 250.0 mg
11                                                                                                                                             paracetamol/acetaminophen 250.0 mg/5 ml
12                                                                                                                                                           paracetamol 250.0 mg/5 ml
13                                                                                                                                                                paracetamol 250.0 mg
14                                                                                                                                                                paracetamol 250.0 mg
15                                                                                                                                                  paracetamol/acetaminophen 500.0 mg
16                                                                                                                                                  paracetamol/acetaminophen 500.0 mg
17                                                                                                                                                  paracetamol/acetaminophen 500.0 mg
18                                                                                                                                                                paracetamol 500.0 mg
19                                                                                                                                                                paracetamol 500.0 mg
20                                                                                                                                                                paracetamol 500.0 mg
21                                                                                                                                                  paracetam

In [54]:
df[df['salts'] == "nan"]

id                                             name  \
33     source_6-75730                            dolo cold syrup 50 ml   
51     source_2-39588                           dolo pain relief spray   
52     source_1-65090                     dolo pain relief spray 35 gm   
138    source_6-75779                           dolocare 100 mg tablet   
149    source_1-65115                            dolocerin tablet 10's   
271    source_6-75824             dolofresh sp 100/500/15 mg tablet 10   
301    source_6-75836                       doloid strip of 10 tablets   
317    source_6-75843                               dolokim capsule 10   
328    source_2-39664                                     dolokind gel   
387    source_6-75871                         dolomec relief gel 30 gm   
392    source_6-75874                         dolomec suspension 60 ml   
414    source_6-75886                      dolomed t 375 mg capsule 10   
430    source_1-65186                   dolomol 125 mg oral suspension   
435    source_6-75895                         dolomol 650 mg tablet 10   
436    source_2-39684                                dolomol iv 100 ml   
458    source_6-75900                             dolonase spray 60 ml   
534    source_6-75929                       dolonip 250 mg syrup 60 ml   
537    source_1-65220                                dolonis gel 30 gm   
545    source_6-75931                  dolop plus 375/325 mg tablet 10   
626    source_1-65249                                 doloral tab 10's   
643    source_6-75964                doloridmr 50/325/250 mg tablet 10   
647    source_1-65259                         dolorin plus tablet 10's   
652    source_1-65261                             dolornilaq injection   
659    source_1-65262                 doloroff ap 100 mg/500 mg tablet   
673    source_1-65267                              doloryl plus tablet   
697    source_1-65270                              dolosal 30 capsules   
700    source_6-75993                            dolosal mr capsule 10   
846    source_6-76043                               doloviz drops 5 ml   
856    source_1-65303                        dolowhite emulsion 100 ml   
857    source_1-65304                         dolowhite emulsion 50 ml   
929    source_1-65322           dolozest mr 250 mg/50 mg/325 mg tablet   
1022  source_2-136315                            zerodol spas 10's tab   
1045  source_2-136319                     zerodol th max 4 tablet 10's   
1059   source_1-11872                             afpincl capsule 10's   
1082  source_1-144845                              nimulid er tab 10's   
1102  source_1-144848             nimulid strong pain relief gel 30 gm   
1103  source_1-144849           nimulid strong pain relief spray 42 gm   
1114   source_2-32466                           corsango d3 suspension   
1117   source_2-32467                                corsangod3 tablet   
1171   source_2-82905                         neovec 4 mg/2 ml inj amp   
1249   source_1-96544                              gutgain sachet 1 gm   
1252  source_6-125694                                insupen ez device   
1253  source_1-103910                               insupen ez pen 1's   
1258  source_6-125696                     insupen pro device 1 numbers   
1259  source_1-103913                                insupen pro green   
1260   source_2-62055                                  insupen pro pen   
1263  source_1-103915                                  insupen red 1's   
1347  source_6-282727                         zocon ont ointment 15 gm   
1368  source_1-161473                       piconet 5 mg oral solution   
1372  source_1-161474                          piconim oral suspension   
1401  source_6-197544                     paracetamol 650 mg tablet 15   
1402   source_2-96301                                  paracetamol inj   
1410   source_2-28249                         ciprofloxacin inj 100 ml   
1413   source_6-53716  

In [55]:
mode_value = df['salts'].mode()[0]  # Get the most frequent value
df.loc[df['salts'] == "nan", 'salts'] = mode_value  # Replace "nan" string with mode

In [56]:
df[df['salts'] == "nan"]

Empty DataFrame
Columns: [id, name, source, prescription_required, retail_price, discounted_price, manufacturer, quantity, packaging_form, salts, base name, dosage form]
Index: []

## Cleaning "packaging_form" column

In [57]:
# Convert the column to lowercase and remove special characters (like "|")
df['packaging_form'] = df['packaging_form'].str.lower().str.replace(r'[^\w\s]', '', regex=True)

In [58]:
df[df["dosage form"] == "tablet"]["packaging_form"]

0                strip
2                  NaN
3        strip  tablet
15               strip
16               strip
17        strip tablet
18                 NaN
19       strip  tablet
20       strip  tablet
21               strip
22               strip
23                 NaN
24       strip  tablet
29                 NaN
32               strip
36               strip
40               strip
41               strip
48               strip
54               strip
55               strip
56                 NaN
57                 NaN
60                 NaN
61       strip  tablet
62                 NaN
63       strip  tablet
64       strip  tablet
67                 NaN
68               strip
71                 NaN
72                 NaN
73               strip
74                 NaN
75               strip
78                 NaN
79               strip
81                 NaN
82       strip  tablet
83       strip  tablet
84                 NaN
85                 NaN
86               strip
87                 NaN
88       strip  tablet
89                 NaN
96               strip
100                NaN
101              strip
102              strip
103                NaN
104                NaN
105                NaN
106              strip
107      strip  tablet
108                NaN
109              strip
110                NaN
111              strip
112      strip  tablet
113                NaN
114              strip
115              strip
116              strip
117      strip  tablet
120      strip  tablet
121                NaN
122                NaN
123                NaN
130                NaN
131              strip
134                NaN
135              strip
136                NaN
137              strip
138              strip
139      strip  tablet
140              strip
141              strip
142                NaN
144              strip
145              strip
146      strip  tablet
147      strip  tablet
148      strip  tablet
149      strip  tablet
150                NaN
151              strip
152                NaN
153      strip  tablet
154              strip
155                NaN
156                NaN
157                NaN
158              strip
159              strip
160                NaN
161              strip
162              strip
163              strip
164                NaN
165      strip  tablet
166              strip
167                NaN
170                NaN
171                NaN
172              strip
174              strip
183      strip  tablet
184                NaN
185                NaN
186              strip
187                NaN
196                NaN
197                NaN
198                NaN
199                NaN
205                NaN
206              strip
207                NaN
208              strip
209      strip  tablet
210                NaN
211              strip
212                NaN
213              strip
214                NaN
215      strip  tablet
216                NaN
217                NaN
220                NaN
222              strip
224      strip  tablet
225      strip  tablet
226                NaN
227                NaN
228                NaN
229      strip  tablet
230              strip
232              strip
233                NaN
234              strip
235                NaN
236              strip
237                NaN
239              strip
240                NaN
241      strip  tablet
244              strip
245                NaN
246                NaN
247                NaN
248      strip  tablet
249                NaN
251                NaN
254              strip
255       strip tablet
256              strip
257                NaN
258      strip  tablet
261                NaN
262      strip  tablet
265      strip  tablet
266                NaN
267              strip
268                NaN
269              strip
271              strip
272                NaN
273              strip
274              strip
275      strip  tablet
276              strip
277                Na

In [59]:
df.loc[(df['dosage form'] == 'tablet') | (df['dosage form'] == 'capsule'), 'packaging_form'] = 'strip'

In [60]:
df.loc[df['dosage form'].isin(ml_dosage_forms) | (df['dosage form'] == 'spray') | (df['dosage form'] == 'oral drop'), 'packaging_form'] = 'bottle'

In [61]:
df.loc[(df['dosage form'] == 'powder') & (df['packaging_form'] != 'sachet'), 'packaging_form'] = 'bottle'

In [62]:
df.loc[(df['dosage form'] == 'soap') | (df['dosage form'] == 'sachet'), 'packaging_form'] = 'sachet'

In [63]:
df.loc[(df['dosage form'] == 'ointment') | (df['dosage form'] == 'cream') | (df['dosage form'] == 'gel'), 'packaging_form'] = 'tube'

In [64]:
df.loc[df['dosage form'] == 'injection', 'packaging_form'] = df.loc[df['dosage form'] == 'injection', 'packaging_form'].apply(
    lambda x: 'ampoule' if 'ampoule' in str(x).lower() else 'vial'
)

In [65]:
df.loc[(df['dosage form'] == 'device'), 'packaging_form'] = 'box'

## Handling missing values in numeric columns retail_price and discounted_price

In [66]:
df['retail_price'].isna().sum()

81

In [67]:
df['discounted_price'].isna().sum()

64

In [68]:
correlation = df[['retail_price', 'discounted_price']].corr()
print(correlation)

                  retail_price  discounted_price
retail_price          1.000000          0.893497
discounted_price      0.893497          1.000000


In [69]:
plt.scatter(df['retail_price'], df['discounted_price'])
plt.title('Retail Price vs Discounted Price')
plt.xlabel('Retail Price')
plt.ylabel('Discounted Price')
plt.show()

In [70]:
df[df['retail_price'].isna() & df['discounted_price'].isna()]

id                                        name    source  \
60     source_7-90352                                dolot tablet  source_7   
77     source_7-90357                     doloage 20 mg injection  source_7   
87     source_7-90361                              dolobak tablet  source_7   
122    source_7-90376            doloby plus 100 mg/500 mg tablet  source_7   
161    source_6-75789         dolocide k plus strip of 10 tablets  source_6   
200    source_6-75801                      dolodil injection 2 ml  source_6   
203    source_6-75802                           dolodol injection  source_6   
220    source_7-90413                            dolofen a tablet  source_7   
227    source_7-90418              dolofirst 375 mg/325 mg tablet  source_7   
233    source_7-90420          doloflam plus 100 mg/500 mg tablet  source_7   
263    source_7-90433                   dolofort 100 mg injection  source_7   
264    source_7-90434                    dolofort 50 mg injection  source_7   
288    source_7-90443                              dologen tablet  source_7   
299    source_7-90447                     dolohit 50 mg injection  source_7   
300    source_7-90448              dolohit p 375 mg/325 mg tablet  source_7   
302    source_6-75837                     doloid suspension 60 ml  source_6   
304    source_7-90450                              dolojoy tablet  source_7   
317    source_6-75843                          dolokim capsule 10  source_6   
364    source_7-90463                   dololsac 50 mg capsule dr  source_7   
413    source_7-90487                  dolomed t 100 mg tablet sr  source_7   
461    source_7-90501                              dolonat tablet  source_7   
528    source_7-90524               dolonim mr 100 mg/2 mg tablet  source_7   
546    source_7-90532             dolop plus 375 mg/325 mg tablet  source_7   
586    source_7-90544                           dolopax d capsule  source_7   
590    source_7-90545                              dolopee tablet  source_7   
592    source_7-90546                    dolopent 30 mg injection  source_7   
596    source_7-90547                     dolopir 20 mg injection  source_7   
618    source_6-75959                doloral 25 mg injection 1 ml  source_6   
627    source_6-75962                           doloran injection  source_6   
632    source_7-90562               dolorest 375 mg/325 mg tablet  source_7   
646    source_7-90571           dolorin 50 mg/10 mg/650 mg tablet  source_7   
653    source_7-90575                      doloroff 125 mg tablet  source_7   
655    source_7-90576                       doloroff 25 mg tablet  source_7   
666    source_6-75975                           doloron injection  source_6   
671    source_7-90582                            dolorylmr tablet  source_7   
676    source_7-90585              dolosacp 25 mg/75 mg injection  source_7   
678    source_7-90586                   dolosacpx 20 mg injection  source_7   
683    source_7-90588                   dolosactr 50 mg injection  source_7   
684    source_6-75984                        dolosac tr injection  source_6   
686    source_7-90589             dolosactrp 375 mg/325 mg tablet  source_7   
688    source_7-90590               dolosafe 375 mg/325 mg tablet  source_7   
689    source_7-90591                           dolosafe d tablet  source_7   
702    source_7-90592              dolosal p 375 mg/325 mg tablet  source_7   
709    source_7-90595                       doloscan 50 mg tablet  source_7   
716    source_7-90601              doloserch 100 mg/375 mg tablet  source_7   
717    source_7-90602                doloserch mf oral suspension  source_7   
721    source_7-90604                           doloset injection  source_7   
738    source_7-90618                dolospan 20 mg/100 mg tablet  source_7   
745    source_7-90620                      dolospan p fizz tablet  source_7   
796    source_7-90643                      doloswift 50 mg tablet  so

## Using KNN to impute values in retail_price column and then since discounted_price is highly correlated to retail_price we are finding average ratio and multiplying that in retail_price to approximate the discounted_price

In [71]:
df[['retail_price', 'discounted_price']] = df[['retail_price', 'discounted_price']].round(2)
knn_imputer = KNNImputer(n_neighbors=3)
df['retail_price'] = knn_imputer.fit_transform(df[['retail_price']])
valid_rows = df.dropna(subset=['retail_price', 'discounted_price'])

# Calculate the average ratio of 'discounted_price' to 'retail_price'
average_ratio = (valid_rows['discounted_price'] / valid_rows['retail_price']).mean()

# Use the average ratio to fill missing 'discounted_price' values
df['discounted_price'] = np.where(df['discounted_price'].isna(),
                                  df['retail_price'] * average_ratio,
                                  df['discounted_price'])

df[['retail_price', 'discounted_price']] = df[['retail_price', 'discounted_price']].round(2)

In [72]:
df.columns

Index(['id', 'name', 'source', 'prescription_required', 'retail_price',
       'discounted_price', 'manufacturer', 'quantity', 'packaging_form',
       'salts', 'base name', 'dosage form'],
      dtype='object')

In [73]:
df['quantity'] = df['quantity'].fillna('Unknown')

In [74]:
df

id  \
0      source_6-75716   
1      source_2-39579   
2      source_7-90343   
3      source_1-65076   
4      source_1-65077   
5      source_6-75717   
6      source_2-39580   
7       source_3-2151   
8      source_7-90345   
9      source_1-65079   
10     source_6-75718   
11      source_3-2152   
12     source_7-90346   
13     source_1-65080   
14     source_1-65081   
15     source_6-75719   
16     source_6-75720   
17      source_3-2153   
18     source_2-39583   
19     source_1-65082   
20     source_1-65083   
21     source_6-75721   
22     source_6-75722   
23     source_2-39584   
24     source_1-65084   
25     source_6-75723   
26     source_6-75724   
27     source_6-75725   
28     source_6-75726   
29     source_2-39585   
30     source_6-75727   
31     source_6-75728   
32     source_6-75729   
33     source_6-75730   
34     source_6-75731   
35     source_7-90348   
36     source_6-75733   
37     source_6-75734   
38     source_1-65085   
39     source_1-65086   
40     source_6-75735   
41     source_6-75736   
42     source_6-75737   
43     source_6-75738   
44     source_7-90349   
45     source_1-65087   
46     source_2-39587   
47     source_1-65088   
48     source_6-75739   
49     source_1-65089   
50     source_6-75740   
51     source_2-39588   
52     source_1-65090   
53     source_1-65091   
54     source_6-75741   
55     source_6-75742   
56     source_2-39589   
57     source_2-39590   
58     source_6-75743   
59     source_1-65092   
60     source_7-90352   
61     source_1-65093   
62     source_7-90353   
63     source_1-65094   
64     source_1-65095   
65     source_2-39591   
66     source_6-75744   
67     source_2-39592   
68     source_6-75745   
69     source_6-75746   
70     source_6-75747   
71     source_2-39593   
72     source_7-90355   
73     source_6-75748   
74     source_7-90356   
75     source_6-75749   
76     source_6-75750   
77     source_7-90357   
78     source_7-90358   
79     source_6-75751   
80     source_6-75752   
81     source_7-90359   
82     source_1-65096   
83     source_1-65097   
84     source_7-90360   
85     source_2-39597   
86     source_6-75753   
87     source_7-90361   
88     source_1-65098   
89     source_7-90362   
90     source_7-90363   
91     source_6-75754   
92     source_2-39598   
93     source_1-65099   
94     source_6-75755   
95     source_6-75756   
96     source_6-75757   
97     source_6-75758   
98     source_6-75759   
99     source_6-75760   
100    source_7-90366   
101    source_6-75761   
102    source_6-75762   
103    source_2-39599   
104    source_2-39600   
105    source_2-39601   
106    source_6-75763   
107    source_1-65101   
108    source_2-39602   
109    source_6-75764   
110    source_7-90371   
111    source_6-75765   
112    source_1-65102   
113    source_7-90372   
114    source_6-75766   
115    source_6-75767   
116    source_6-75768   
117    source_1-65103   
118    source_6-75769   
119    source_2-39605   
120    source_1-65104   
121    source_7-90375   
122    source_7-90376   
123    source_7-90377   
124    source_7-90379   
125    source_6-75771   
126    source_1-65107   
127    source_6-75772   
128    source_1-65108   
129    source_7-90380   
130    source_7-90381   
131    source_6-75774   
132    source_6-75775   
133    source_6-75776   
134    source_7-90383   
135    source_6-75777   
136    source_7-90384   
137    source_6-75778   
138    source_6-75779   
139    source_1-65111   
140    source_6-75780   
141    source_6-75781   
142    source_2-39609   
143    source_6-75782   
144    source_6-75783   
145    source_6-75784   
146    source_1-65112   
147    source_1-65113   
148    source_1-65114   
149    source_1-65115   
150    source_2-39610   
151    source_6-75785   
152    source_7-90389   
153    source_1-65116   
154    source_6-75786   
155    source_2-39611   
156    source_2-39612   
157    source_7-90392   
158    source_6-75787   
159    source_6-757

In [75]:
df.to_csv("data.csv", index=False)

In [76]:
from google.colab import files
files.download("data.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [77]:
df.columns

Index(['id', 'name', 'source', 'prescription_required', 'retail_price',
       'discounted_price', 'manufacturer', 'quantity', 'packaging_form',
       'salts', 'base name', 'dosage form'],
      dtype='object')

# Clustering

In [78]:
remove_words = ['mg', 'ml', 'ww', 'na', 'wv', 'vv', 'vw', 'gm']

# Apply transformations
df['salts'] = df['salts'].apply(lambda x: re.sub(r'[^a-zA-Z\s]', ' ', x))  # Remove numbers and special characters
df['salts'] = df['salts'].apply(lambda x: re.sub(r'\b(?:' + '|'.join(remove_words) + r')\b', '', x))  # Remove specific words (mg, ml, ww)
df['salts'] = df['salts'].apply(lambda x: re.sub(r'\b[a-zA-Z]\b', '', x))
df['salts'] = df['salts'].apply(lambda x: re.sub(r'\s+', ' ', x))  # Replace multiple spaces with a single space
df['salts'] = df['salts'].str.strip()  # Remove leading/trailing spaces

In [79]:
df['salts']

0                                                                                                   paracetamol acetaminophen
1                                                                                                   paracetamol acetaminophen
2                                                                                                                 paracetamol
3                                                                                                                 paracetamol
4                                                                                                                 paracetamol
5                                                                                                   paracetamol acetaminophen
6                                                                                                   paracetamol acetaminophen
7                                                                                                   paracetamol acetaminophen
8                                                                                                                 paracetamol
9                                                                                                                 paracetamol
10                                                                                                  paracetamol acetaminophen
11                                                                                                  paracetamol acetaminophen
12                                                                                                                paracetamol
13                                                                                                                paracetamol
14                                                                                                                paracetamol
15                                                                                                  paracetamol acetaminophen
16                                                                                                  paracetamol acetaminophen
17                                                                                                  paracetamol acetaminophen
18                                                                                                                paracetamol
19                                                                                                                paracetamol
20                                                                                                                paracetamol
21                                                                                                  paracetamol acetaminophen
22                                                                                                  paracetamol acetaminophen
23                                                                                                                paracetamol
24                                                                                                                paracetamol
25                                                                                                  paracetamol acetaminophen
26                                                                                                  paracetamol acetaminophen
27                                                    phenylephrine chlorpheniramine chlorphenamine paracetamol acetaminophen
28                                                  chlorpheniramine chlorphenamine pseudoephedrine paracetamol acetaminophen
29                                                                                    paracetamol acetaminophen caffeine phen
30                                                                                                             xylometazoline
31                                                                                            

## Clustering only on "salts" column

In [144]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score

# Step 1: Vectorizing the 'salts' column using BoW
vectorizer = CountVectorizer(stop_words='english', max_features=100)  # Adjust `max_features` as needed
X_salts = vectorizer.fit_transform(df['salts'])

# Step 2: Convert sparse matrix to dense
X_salts_dense = X_salts.toarray()

# Step 3: Normalize the data
scaler = StandardScaler()
X_salts_scaled = scaler.fit_transform(X_salts_dense)

# Step 4: Apply clustering (e.g., KMeans)
kmeans = KMeans(n_clusters=3, random_state=42)  # Change number of clusters as needed
df['cluster_salts'] = kmeans.fit_predict(X_salts_scaled)

# Step 5: Evaluate Clustering (Optional)
silhouette_avg = silhouette_score(X_salts_scaled, df['cluster_salts'])
print(f'Silhouette Score: {silhouette_avg}')

Silhouette Score: 0.6316527928375562
